# Uso de Apache Fuseki con datos Orion

## Instalación de las librerias necesarias

In [1]:
!pip install rdflib
!pip install rdflib-jsonld
!pip install SPARQLWrapper
!pip install pandas

DEPRECATION: Loading egg at c:\users\marie\appdata\local\programs\python\python311\lib\site-packages\skfeature-1.0.0-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


DEPRECATION: Loading egg at c:\users\marie\appdata\local\programs\python\python311\lib\site-packages\skfeature-1.0.0-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


DEPRECATION: Loading egg at c:\users\marie\appdata\local\programs\python\python311\lib\site-packages\skfeature-1.0.0-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


DEPRECATION: Loading egg at c:\users\marie\appdata\local\programs\python\python311\lib\site-packages\skfeature-1.0.0-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation.. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [8]:
from SPARQLWrapper import SPARQLWrapper, JSON, POST
import requests
from rdflib import Graph
from rdflib.serializer import Serializer

## Configuración inicial

En este código creamos la base de datos en Apache Fuseki, solo es necesario la primera vez

In [9]:
from requests.auth import HTTPBasicAuth
fuseki_url = "http://localhost:3030/$/datasets"
database_name = "prueba"
data = {
    "dbName": database_name,
    "dbType": "tdb2"
}
headers = {
    "Content-Type": "application/x-www-form-urlencoded",
}

username = "admin"  # Reemplaza con tu nombre de usuario
password = "admin"

# Realizar la solicitud POST para crear la base de datos
response = requests.post(fuseki_url, data=data, headers=headers, auth=HTTPBasicAuth(username, password))

# Verificar la respuesta
if response.status_code == 200:
    print(f"Base de datos '{database_name}' creada exitosamente.")
else:
    print(f"Error al crear la base de datos '{database_name}'.")
    print(f"Estado: {response.status_code}")
    print(f"Respuesta: {response.text}")

Error al crear la base de datos 'prueba'.
Estado: 409
Respuesta: Name already registered /prueba



Aqui encontramos los parametros que definen la conexión con nuestro servidor Apache Fuseki y con el Orion Context Broker

In [10]:
orion_url = "http://localhost:1026/ngsi-ld/v1/entities"
fuseki_url = "http://localhost:3030/prueba"

sparql_connection = SPARQLWrapper(fuseki_url+"/query")
sparql_connection_update = SPARQLWrapper(fuseki_url)

## Funciones empleadas

En este apartado encontramos las distintas funciones que emplearemos para crear nuestro Gráfico de conocimiento a partir de los datos de Orion y algunas consultas para probar su funcionamiento

### Checkeo de si una entidad esta presente en Fuseki

In [11]:
def check_entity_exist(sparql_connection,entity_id):
    sparql = sparql_connection
    query = """
    ASK WHERE {{
      <{0}> ?p ?o
    }}
""".format(entity_id)
    sparql.setHTTPAuth('BASIC')
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    results = sparql.query().convert()
    return results['boolean']

### Funciones para la obtención de las entidades de orion

In [12]:
def get_orion_entities(orion_url, entity_type, offset=0, limit=1000):
    headers = {
        "Link":"<https://raw.githubusercontent.com/mariete1223/MarMenor/main/data_models_description/datamodels.context-ngsi.jsonld>",
        "Accept": "application/ld+json",
        "rel": "http://www.w3.org/ns/json-ld#context"
    }
    orion_url = orion_url + "?type=" + entity_type+"&limit="+str(limit)+"&offset="+str(offset)
    # Obtener entidades desde Orion Context Broker
    response = requests.get(orion_url, headers=headers)
    entities = response.json()
    return entities

### Subscripción a entidad de Orion

In [13]:
def crear_subscription(description, entity_type, url, orion_url_subscription, sent_attributes = None, watched_attributes = None, ):
    subscription_content = {
        "description": description,
        "type": "Subscription",
        "entities": [{"type": entity_type}],
        "notification": {
            "endpoint": {
                "uri": url,
                "accept":  "application/json"
            }
        },
        "@context": "https://raw.githubusercontent.com/mariete1223/MarMenor/main/data_models_description/datamodels.context-ngsi.jsonld"
    }

    if watched_attributes is not None:
        subscription_content["watchedAttributes"] = watched_attributes
    if sent_attributes is not None:
        subscription_content["notification"]["attributes"] = sent_attributes

    url = orion_url_subscription

    headers = {
        "Content-Type": "application/ld+json"
    }

    response = requests.post(url, headers=headers, json=subscription_content)
    print(response)

### Modificación de una entidad de Orion

In [14]:
import math
def modify_device_measurement( value, observedAt, unitcode, url, depth = None, place = None, isComposedOf = False):

    headers = {
        'Content-Type': 'application/json',
        'Link': '<https://raw.githubusercontent.com/mariete1223/MarMenor/main/data_models_description/datamodels.context-ngsi.jsonld>; rel="http://www.w3.org/ns/json-ld#context"; type="application/ld+json"'
    }

    if isinstance(value, float) and  math.isnan(value):
        value = -99

    modify_content = {
        "numValue": {
            "type": "Property",
            "value": value,
            "observedAt": observedAt
        },
        "dateLastValueReported": {
            "type": "Property",
            "value": observedAt
        }
    }

    if depth is not None:
        modify_content["numValue"]["depth"] = {
            "type": "Property",
            "value": depth
        }
    
    if place is not None:
        modify_content["numValue"]["measurementPlace"] = {
            "type": "Property",
            "value": place
        }

    if unitcode is not None:
        modify_content["numValue"]["unitCode"] = unitcode

    if isComposedOf:
        modify_content = {
            "isComposedOf": value
        }


    print("modify_content")
    print(modify_content)
    response = requests.patch(url, headers=headers, json=modify_content)
    print(response.status_code)
    try:
        if response.status_code != 204:
            print(response.text)
    finally:
        response.close()

### Inserción de entidades en Fuseki

In [15]:
def insert_entity(entity):
    if(check_entity_exist(sparql_connection,entity['id'])):
        print("La entidad ya existe en Fuseki.")
        return
    g = Graph()
    jsonld_data_context = entity['@context']
    contexts = []
    contexts.append(jsonld_data_context)
    contexts.append("https://uri.etsi.org/ngsi-ld/v1/ngsi-ld-core-context.jsonld")
    entity['@context'] = contexts
    g.parse(data=entity, format='json-ld')
    fuseki_data = g.serialize(format='turtle')
    headers = {'Content-Type': 'text/turtle'}
    print(fuseki_data)
    response = requests.post(fuseki_url+"/data", data=fuseki_data, headers=headers, auth=('admin', 'admin'))
    if response.status_code == 200:
        print("Datos cargados exitosamente en Fuseki.")
    else:
        print("Error al cargar datos en Fuseki:", response.text)

### Eliminación de todas las entidades en Fuseki

In [16]:
def delete_all():
    query = """
        CLEAR ALL
    """

    sparql_connection_update.setMethod(POST)
    # Establecer la consulta SPARQL en el objeto SPARQLWrapper
    sparql_connection_update.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection_update.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection_update.query().convert()

    results

### Obtención de diferentes entidades de Fuseki

In [17]:
def getBuoy(buoy_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/>
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX ns1: <https://smartdatamodels.org/>
    PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
    SELECT ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2 (GROUP_CONCAT(?meas; SEPARATOR=",") AS ?measurements) (GROUP_CONCAT(?cm; SEPARATOR=",") AS ?closeMeasurements)
    WHERE {{
        ?entity a <https://raw.githubusercontent.com/mariete1223/MarMenor/main/Buoy/buoy.yaml#/Buoy> ;
                ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
                ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
                ns1:address [ ngsi-ld:hasValue [ ns1:addressCountry ?addressCountry ;
                            ns1:addressLocality ?addressLocality ;
                            ns1:addressRegion ?addressRegion ;
                            ns1:postalCode ?postal ] ] ;
                ns1:source [ ngsi-ld:hasValue ?source ] ;
                ngsi-ld:description [ ngsi-ld:hasValue ?description ] ;
                ngsi-ld:location [ ngsi-ld:hasValue [ ngsi-ld:coordinates ?coordinates1 ;
                                                    ngsi-ld:coordinates ?coordinates2  ] ] .
                FILTER(?coordinates1 > ?coordinates2)
                OPTIONAL {{
                    ?entity ns2:closeMeasurements  [ a ngsi-ld:Property ;
                                                    ngsi-ld:hasValue [ ngsi-ld:hasObject ?cm ] ] ;
                            ngsi-ld:hasMeasurement [ a ngsi-ld:Relationship ;
                                        ngsi-ld:hasObject ?meas ]
                            
                }}
    }}
    GROUP BY ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2
    """.format(buoy_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [18]:
def getRavine(ravine_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/>
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX ns1: <https://smartdatamodels.org/>
    PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/Ravine/ravine.yaml#/>
    PREFIX ns3: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
    PREFIX sch: <https://schema.org/>

    SELECT ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2 ?section ?previousSection ?nextSection ?waterNetwork (GROUP_CONCAT(?meas; SEPARATOR=",") AS ?measurements) (GROUP_CONCAT(?cm; SEPARATOR=",") AS ?closeMeasurements)
    WHERE {{
        ?entity a <https://raw.githubusercontent.com/mariete1223/MarMenor/main/Ravine/ravine.yaml#/Ravine> ;
                ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
                ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
                ns1:address [ ngsi-ld:hasValue [ ns1:addressCountry ?addressCountry ;
                            ns1:addressLocality ?addressLocality ;
                            ns1:addressRegion ?addressRegion ;
                            ns1:postalCode ?postal ] ] ;
                ns1:source [ ngsi-ld:hasValue ?source ] ;
                ngsi-ld:description [ ngsi-ld:hasValue ?description ] ;
                ngsi-ld:location [ ngsi-ld:hasValue [ ngsi-ld:coordinates ?coordinates1 ;
                                                    ngsi-ld:coordinates ?coordinates2  ] ] .
                FILTER(?coordinates1 > ?coordinates2)
                OPTIONAL {{
                    ?entity ns2:section [ ngsi-ld:hasValue ?section ] ;
                            ns2:previousSection [ ngsi-ld:hasValue ?previousSection ] ;
                            ns2:nextSection [ ngsi-ld:hasValue ?nextSection ] ;
                            ns3:closeMeasurements  [ a ngsi-ld:Property ;
                                                    ngsi-ld:hasValue [ ngsi-ld:hasObject ?cm ] ] ;
                            sch:isPartOf [ ngsi-ld:hasObject ?waterNetwork ] ;
                            ngsi-ld:hasMeasurement [ a ngsi-ld:Relationship ;
                                        ngsi-ld:hasObject ?meas ]
                }}
    }}
    GROUP BY ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2 ?section ?previousSection ?nextSection ?waterNetwork
    """.format(ravine_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [19]:
def getSoundingPlace(sounding_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/>
PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
PREFIX ns1: <https://smartdatamodels.org/>
PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
PREFIX sch: <https://schema.org/>

SELECT ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2 ?numberInNetwork ?piezometricNet (GROUP_CONCAT(?meas; SEPARATOR=",") AS ?measurements) (GROUP_CONCAT(?cm; SEPARATOR=",") AS ?closeMeasurements)
WHERE {{
    ?entity a <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/SoundingPlace> ;
            ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
            ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
            ns1:address [ ngsi-ld:hasValue [ ns1:addressCountry ?addressCountry ;
                        ns1:addressLocality ?addressLocality ;
                        ns1:addressRegion ?addressRegion ;
                        ns1:postalCode ?postal ] ] ;
            ns1:source [ ngsi-ld:hasValue ?source ] ;
            ngsi-ld:description [ ngsi-ld:hasValue ?description ] ;
            ngsi-ld:location [ ngsi-ld:hasValue [ ngsi-ld:coordinates ?coordinates1 ;
                                                ngsi-ld:coordinates ?coordinates2  ] ] .
            FILTER(?coordinates1 > ?coordinates2)
            OPTIONAL {{
                ?entity ns2:numberInNetwork [ ngsi-ld:hasValue ?numberInNetwork ] ;
                        ns2:closeMeasurements  [ a ngsi-ld:Property ;
                                                    ngsi-ld:hasValue [ ngsi-ld:hasObject ?cm ] ] ;
                        sch:isPartOf [ ngsi-ld:hasObject ?piezometricNet ] ;
                        ngsi-ld:hasMeasurement [ a ngsi-ld:Relationship ;
                                        ngsi-ld:hasObject ?meas ]
            }}
}}
GROUP BY ?entity ?name ?location ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?coordinates1 ?coordinates2 ?numberInNetwork ?piezometricNet
    """.format(sounding_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [20]:
def getDeviceMeasurement(devicemeas_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/>
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX ns1: <https://smartdatamodels.org/>
    PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
    PREFIX sch: <https://schema.org/>
    PREFIX devm: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>

    SELECT ?entity ?name ?source ?controlledProperty ?deviceType ?numValue ?observedAt ?depth ?target ?refDevice
    WHERE {{
        ?entity a <https://smartdatamodels.org/dataModel.DeviceMeasurement/DeviceMeasurement> ;
                ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
                ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
                ns1:source [ ngsi-ld:hasValue ?source ] ;
                ns1:controlledProperty [ ngsi-ld:hasValue ?controlledProperty ] ;
                devm:deviceType [ ngsi-ld:hasValue ?deviceType ] ;
                devm:numValue [ ngsi-ld:hasValue ?numValue ;
                                ngsi-ld:observedAt ?observedAt ] ;
                devm:refDevice [ ngsi-ld:hasObject ?refDevice ] ;
                            
                OPTIONAL {{
                ?entity ns1:target [ ngsi-ld:hasValue ?target ] .
                }}
                OPTIONAL {{
                    ?entity ns1:depth [ ngsi-ld:hasValue ?depth ] .
                }}
    }}
    """.format(devicemeas_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [21]:
def getPiezometricNet(device_piezometric_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/> 
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 
    PREFIX ns1: <https://smartdatamodels.org/> 
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 

    SELECT ?entity ?name ?addressCountry ?addressLocality ?addressRegion ?postal ?source ?description ?location
    WHERE {{
        ?entity a <https://raw.githubusercontent.com/mariete1223/MarMenor/main/PiezometricNet/piezometricNet.yaml#/PiezometricNet> ;
                ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
                ns1:address [ ngsi-ld:hasValue [ ns1:addressCountry ?addressCountry ;
                        ns1:addressRegion ?addressRegion ] ] ;
                ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
                ns1:source [ ngsi-ld:hasValue ?source ] ;
                ngsi-ld:description [ ngsi-ld:hasValue ?description ] ;
                ngsi-ld:location [ a ngsi-ld:GeoProperty ;
                        ngsi-ld:hasValue ?location ] ;
    }}
    """.format(device_piezometric_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [22]:
def getWaterNetwork(water_network_id):
    query = """
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/> 
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 
    PREFIX ns1: <https://smartdatamodels.org/> 
    PREFIX ns2: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/> 
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 

    SELECT ?name ?addressCountry ?addressLocality ?addressRegion ?postal ?description ?location (GROUP_CONCAT(?values; SEPARATOR=",") AS ?isComposedOf)
    WHERE {{
        <{0}> a ns2:WaterNetwork ;
                ns1:address [ ngsi-ld:hasValue [ ns1:addressCountry ?addressCountry ;
                        ns1:addressRegion ?addressRegion ] ] ;
                ns2:isComposedOf [ a ngsi-ld:Property ;
                        ngsi-ld:hasValue [ a ngsi-ld:Relationship ;
                                ngsi-ld:hasObject ?values ] ] ;
                ngsi-ld:name [ ngsi-ld:hasValue ?name ] ;
                ngsi-ld:description [ ngsi-ld:hasValue ?description ] ;
                ngsi-ld:location [ a ngsi-ld:GeoProperty ;
                        ngsi-ld:hasValue ?location ] ;
    }}
    GROUP BY ?name ?addressCountry ?addressLocality ?addressRegion ?postal ?description ?location
    """.format(water_network_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [23]:
def getDevice(device_id):
    query = """
        PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/> 
        PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 
        PREFIX ns1: <https://smartdatamodels.org/dataModel.Device/> 
        PREFIX ns2: <https://smartdatamodels.org/> 
        PREFIX ns3: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/>
        PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 

        SELECT ?entity ?name ?addressCountry ?addressLocality ?addressRegion ?postalCode 
               (GROUP_CONCAT(?controlledProperty; SEPARATOR=",") AS ?controlledProperties) 
               ?controlledAsset ?deviceCategory ?alternateName ?areaServed ?dateLastValueReported 
               ?source ?description ?coordinates1 ?coordinates2
        WHERE {{
                ?entity a <https://smartdatamodels.org/dataModel.Device/Device> ;
                        ns2:identifier [ ngsi-ld:hasValue "{0}" ] ;
                        ns2:address [ 
                        ngsi-ld:hasValue [ ns2:addressCountry ?addressCountry ;
                                ns2:addressLocality ?addressLocality ;
                                ns2:addressRegion ?addressRegion ;
                                ns2:postalCode ?postalCode ] ] ;
                        ns2:controlledProperty [ 
                                ngsi-ld:hasValue ?controlledProperty ] ;
                        ns1:controlledAsset [ 
                                ngsi-ld:hasObject ?controlledAsset ] ;
                        ns1:deviceCategory [ 
                                ngsi-ld:hasValue ?deviceCategory ] ;
                        ns3:alternateName [ 
                                ngsi-ld:hasValue ?alternateName ] ;
                        ns3:areaServed [ 
                                ngsi-ld:hasValue ?areaServed ] ;
                        ns2:dateLastValueReported [ 
                                ngsi-ld:hasValue ?dateLastValueReported ] ;
                        ns2:source [ 
                                ngsi-ld:hasValue ?source ] ;
                        ngsi-ld:description [ 
                                ngsi-ld:hasValue ?description ] ;
                        ngsi-ld:name [ 
                                ngsi-ld:hasValue ?name ] ;
                        ngsi-ld:location [ ngsi-ld:hasValue [ ngsi-ld:coordinates ?coordinates1 ;
                                                        ngsi-ld:coordinates ?coordinates2  ] ] .
                        FILTER(?coordinates1 > ?coordinates2)
                
    }}
    GROUP BY ?entity ?name ?addressCountry ?addressLocality ?addressRegion ?postalCode 
             ?controlledAsset ?deviceCategory ?alternateName ?areaServed ?dateLastValueReported 
             ?source ?description ?coordinates1 ?coordinates2
    """.format(device_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return results["results"]["bindings"][0]

In [24]:
def getDeviceControlledProperties(device_id):
    query = """
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX ns1: <https://smartdatamodels.org/>
    PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
    PREFIX sch: <https://schema.org/>
    PREFIX devm: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>
    PREFIX ns3: <https://smartdatamodels.org/dataModel.Device/>
    PREFIX ns4: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/>

    SELECT ?controlledProperty
    WHERE {{
        ?entity a <https://smartdatamodels.org/dataModel.Device/Device> ;
                ns1:identifier [ ngsi-ld:hasValue "{0}" ] ;
                ns1:controlledProperty [ ngsi-ld:hasValue ?controlledProperty ] ;
    }}
""".format(device_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    if len(results["results"]["bindings"]) == 0:
        return {"error": "no results found"}

    return [result["controlledProperty"]["value"] for result in results["results"]["bindings"]]

In [25]:
def getEntityControlledProperties(entity_id):
    query = """
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX ns1: <https://smartdatamodels.org/>
    PREFIX ns2: <https://raw.githubusercontent.com/mariete1223/MarMenor/main/SoundingPlace/soundingPlace.yaml#/>
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#>
    PREFIX sch: <https://schema.org/>
    PREFIX devm: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>
    PREFIX ns3: <https://smartdatamodels.org/dataModel.Device/>
    PREFIX ns4: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/>

    SELECT ?controlledProperty
    WHERE {{
        ?entity a <https://smartdatamodels.org/dataModel.Device/Device> ;
                ns3:controlledAsset [ ngsi-ld:hasObject <{0}> ] ;
                ns1:controlledProperty [ ngsi-ld:hasValue ?controlledProperty ] ;
    }}
""".format(entity_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    return [result["controlledProperty"]["value"] for result in results["results"]["bindings"]]

### Busqueda entidades que cumplen un filtro

Esta funcion devuelve las entidades que contengan la cadena especificada en el nombre

In [76]:
def query_by_name(param_value):
    # Definir la consulta SPARQL con los parámetros adecuados
    query = f"""
    PREFIX ns1: <https://smartdatamodels.org/> 
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 

    SELECT ?entity 
    WHERE {{
        ?entity ngsi-ld:name [ a ngsi-ld:Property ;
                        ngsi-ld:hasValue ?value ] .
        FILTER(CONTAINS(?value, "{param_value}"))
    }}

    """

    # Crear una instancia de SPARQLWrapper
    sparql_connection.setQuery(query)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    results = [ results["results"]["bindings"][i]["entity"]["value"] for i in range(len(results["results"]["bindings"]))]

    # {'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:Device:001'}}

    return results

Esta funcion devuelve las entidades que contengan la cadena especificada el parametro de tipo propiedad especificado

In [97]:
def query_sparql_by_poperty_parameter(param_prefix,param_name, param_value):
    # Definir la consulta SPARQL con los parámetros adecuados
    query = f"""
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/> 
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 
    PREFIX ns1: <https://smartdatamodels.org/> 
    PREFIX ns2: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/> 
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 
    PREFIX param: <{param_prefix}>

    SELECT ?entity
    WHERE {{
        ?entity param:{param_name} [ ngsi-ld:hasValue ?value ] ;
        FILTER (CONTAINS(str(?value), "{param_value}"))
    }}
    GROUP BY ?entity ?name ?addressCountry ?addressLocality ?addressRegion ?postal ?description ?location
    """

    # Crear una instancia de SPARQLWrapper
    sparql_connection.setQuery(query)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    results = [ results["results"]["bindings"][i]["entity"]["value"] for i in range(len(results["results"]["bindings"]))]

    return results

Esta funcion devuelve las entidades que contengan la cadena especificada el parametro de tipo relación especificado

In [102]:
def query_sparql_by_relation_parameter(param_prefix,param_name, param_value):
    # Definir la consulta SPARQL con los parámetros adecuados
    query = f"""
    PREFIX : <https://uri.etsi.org/ngsi-ld/default-context/> 
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/> 
    PREFIX ns1: <https://smartdatamodels.org/> 
    PREFIX ns2: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/> 
    PREFIX xsd: <http://www.w3.org/2001/XMLSchema#> 
    PREFIX param: <{param_prefix}>

    SELECT ?entity
    WHERE {{
        ?entity param:{param_name} [ ngsi-ld:hasObject ?value ] ;
        FILTER (CONTAINS(str(?value), "{param_value}"))
    }}
    GROUP BY ?entity ?name ?addressCountry ?addressLocality ?addressRegion ?postal ?description ?location
    """

    # Crear una instancia de SPARQLWrapper
    sparql_connection.setQuery(query)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    results = [ results["results"]["bindings"][i]["entity"]["value"] for i in range(len(results["results"]["bindings"]))]

    return results

### Adición de atributos a entidades

Funciones empleadas para incorporar un atributo de interes para nuestro caso particular en nuestro Apache Fuseki

#### Función que añade las medidas asociadas a esa entidad

Asocia los DeviceMeasurements a su entidad correspondiente

In [31]:
def add_measurements_to_entity(id_entity):
    query = """
        PREFIX ns1: <http://www.w3.org/1999/xhtml/vocab#>
        PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
        PREFIX ns3: <https://smartdatamodels.org/dataModel.Device/>
        PREFIX smd: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>

        DELETE {{
            <{0}> ngsi-ld:hasMeasurement ?borrar .
        }}
        INSERT {{
            <{0}> ngsi-ld:hasMeasurement [ a ngsi-ld:Relationship ;
                                        ngsi-ld:hasObject ?measurement ] .
        }}
        WHERE {{
            OPTIONAL {{
                <{0}> ngsi-ld:hasMeasurement ?borrar .
            }}
            ?measurement a smd:DeviceMeasurement ;
        smd:refDevice/ngsi-ld:hasObject/ns3:controlledAsset/ngsi-ld:hasObject <{0}> .
        }}
    """.format(id_entity)
    # Establecer la consulta y el formato de salida

    sparql_connection_update.setMethod(POST)
    sparql_connection_update.setQuery(query)
    sparql_connection_update.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection_update.query().convert()
    return results

#### Función que añade las medidas asociadas a esa entidad de una propiedad concreta 

Asocia los DeviceMeasurements de una propiedad concreta a su entidad correspondiente

In [32]:
def add_measurements_controlled_property_to_entity(id_entity, controlled_property):
    query = """
        PREFIX ns1: <http://www.w3.org/1999/xhtml/vocab#>
        PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
        PREFIX ns3: <https://smartdatamodels.org/dataModel.Device/>
        PREFIX smd: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>
        PREFIX sm: <https://smartdatamodels.org/>

        INSERT {{
            <{0}> ngsi-ld:has{1} ?measurement .
        }}
        WHERE {{
            ?measurement a smd:DeviceMeasurement ;
        smd:refDevice/ngsi-ld:hasObject/ns3:controlledAsset/ngsi-ld:hasObject <{0}> ;
        sm:controlledProperty/ngsi-ld:hasValue "{1}" .
        }}
    """.format(id_entity,controlled_property)
    # Establecer la consulta y el formato de salida
    sparql_connection_update.setMethod(POST)
    sparql_connection_update.setQuery(query)
    sparql_connection_update.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection_update.query().convert()
    return results 

### Obtención atributos de una entidad

In [62]:
def getProperties(entity_id):
    query = """
    SELECT ?pred WHERE {{
    <{0}> ?pred ?obj .
    }}
    """.format(entity_id)

    sparql_connection.setQuery(query)

    # Establecer el formato de salida de los resultados (en este caso, JSON)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()

    fina_results = [ res["pred"]["value"] for res in results["results"]["bindings"]]

    return set(fina_results[1:])

### Trabajando con measurements de una entidad añadidos anteriormente

A continuación una serie de funciones que nos permite obtener los valores asociados a las relaciones que se han definido anteriormente

#### Función para obtener los valores de las medidas asociadas a la entidad

In [55]:
def get_values_measurements(id_entity):
    query = """
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX devm: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>
    PREFIX ns1: <https://smartdatamodels.org/>

    SELECT ?measurement ?numValue ?controlledProperty ?observedAt ?target ?depth
    WHERE {{
      <{0}> ngsi-ld:hasMeasurement [ ngsi-ld:hasObject ?measurement ] .
      ?measurement devm:numValue [ ngsi-ld:hasValue ?numValue ] .
      ?measurement ns1:controlledProperty [ ngsi-ld:hasValue ?controlledProperty ] .
      ?measurement devm:numValue [
        ngsi-ld:hasValue ?numValue ;
        ngsi-ld:observedAt ?observedAt
      ] .
      OPTIONAL {{
          ?measurement ns1:target [ ngsi-ld:hasValue ?target ] .
      }}
      OPTIONAL {{
          ?measurement ns1:depth [ ngsi-ld:hasValue ?depth ] .
      }}
    }}
    """.format(id_entity)

    sparql_connection.setMethod(POST)
    sparql_connection.setQuery(query)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    return results["results"]["bindings"]

#### Función para obtener los valores de las medidas de una propiedad concreta

In [56]:
def get_values_measurements_controlled(id_entity, controlled_property):
    properties = getProperties(id_entity)

    if f"https://uri.etsi.org/ngsi-ld/has{controlled_property}" not in properties:
        return "No existe el atributo"
    query = """
    PREFIX ngsi-ld: <https://uri.etsi.org/ngsi-ld/>
    PREFIX devm: <https://smartdatamodels.org/dataModel.DeviceMeasurement/>
    PREFIX sm: <https://smartdatamodels.org/>

    SELECT ?measurement ?numValue ?observedAt ?depth ?target
    WHERE {{
      <{0}> ngsi-ld:has{1} ?measurement .
      ?measurement devm:numValue [
        ngsi-ld:hasValue ?numValue ;
        ngsi-ld:observedAt ?observedAt
      ] .
      OPTIONAL {{
      ?measurement sm:depth [
        ngsi-ld:hasValue ?depth
      ] .
      }}
      OPTIONAL {{
        ?measurement sm:target [
          ngsi-ld:hasValue ?target
        ] .
      }}
    }}
    """.format(id_entity,controlled_property)

    sparql_connection.setQuery(query)
    sparql_connection.setReturnFormat(JSON)

    # Ejecutar la consulta y obtener los resultados
    results = sparql_connection.query().convert()
    return results["results"]["bindings"]

## Uso de las funciones anteriores para el despliegue de Fuseki

Hay que configurar correctamente las urls y el nombre de nuestra base de datos correctamente en la sección inicial, la configuración inicial por defecto es la siguiente:

orion_url = "http://localhost:1026/ngsi-ld/v1/entities" 

fuseki_url = "http://localhost:3030/prueba"

graph_uri = "http://example.com/graph"

sparql_connection = SPARQLWrapper(fuseki_url+"/query")

sparql_connection_update = SPARQLWrapper(fuseki_url)º

### Comenzamos borrando todas las entidades para asegurar que no hay nada en nuestra base de datos

In [18]:
delete_all()

### Realizamos las consultas a Orion y las subimos a Fuseki

Para los tipos de entidades indicados en `entity_types` se realizan las consultas en Orion y luego se suben a Fuseki, comprobando si la entidad existe anteriormente o no.

In [89]:
entity_types = ["Device","DeviceMeasurement","Ravine","SoundingPlace","Buoy","WaterNetwork","PiezometricNet"]

for entity_type in entity_types:
    print("Obteniendo entidades de tipo:", entity_type)
    offset = 0
    limit = 999
    first=True
    while first or (len(entities) == (limit)):
        first=False
        entities = get_orion_entities(orion_url, entity_type, offset=offset, limit=limit)
        print("Entidades obtenidas:", len(entities))
        for entity in entities:
            print("Insertando entidad:", entity['id'])
            insert_entity(entity)
        offset = offset + limit


Obteniendo entidades de tipo: Device
Entidades obtenidas: 44
Insertando entidad: urn:ngsi-ld:Device:000
@prefix : <https://uri.etsi.org/ngsi-ld/default-context/> .
@prefix ngsi-ld: <https://uri.etsi.org/ngsi-ld/> .
@prefix ns1: <https://smartdatamodels.org/> .
@prefix ns2: <https://smartdatamodels.org/dataModel.Device/> .
@prefix ns3: <https://smartdatamodels.org/dataModel.WaterDistributionManagementEPANET/> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

<urn:ngsi-ld:Device:000> a ns2:Device ;
    ns1:address [ a ngsi-ld:Property ;
            :verified [ a ngsi-ld:Property ;
                    ngsi-ld:hasValue true ] ;
            ngsi-ld:hasValue [ ns1:addressCountry "ES" ;
                    ns1:addressLocality "Mar Menor, San Javier, Cartagena" ;
                    ns1:addressRegion "Murcia" ;
                    ns1:postalCode "30380" ] ] ;
    ns1:controlledProperty [ a ngsi-ld:Property ;
            ngsi-ld:hasValue "chlorophyll",
                "conductivity",
      

### Comprobamos la obtención de entidades para comprobar que se ha subido correctamente

In [90]:
getBuoy("urn:ngsi-ld:Buoy:001")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:Buoy:001'},
 'name': {'type': 'literal', 'value': 'Buoy E10'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressLocality': {'type': 'literal',
  'value': 'Mar Menor, Los Nietos, Cartagena'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'postal': {'type': 'literal', 'value': '30383'},
 'source': {'type': 'literal',
  'value': 'https://idearm.imida.es/cgi/siomctdmarmenor/#CTD-E10'},
 'description': {'type': 'literal',
  'value': 'Buoy E10 for measuring water quality in the Mar Menor'},
 'coordinates1': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '37.65e0'},
 'coordinates2': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '-0.78e0'}}

In [110]:
getPiezometricNet("urn:ngsi-ld:PiezometricNet:000")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:PiezometricNet:000'},
 'name': {'type': 'literal', 'value': 'Piezometric Network of the Mar Menor'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'source': {'type': 'literal', 'value': 'http://155.54.95.167/'},
 'description': {'type': 'literal',
  'value': 'Piezometric Network of the Mar Menor, composed of several boreholes in the coastal area.'},
 'location': {'type': 'bnode', 'value': 'b0'}}

In [91]:
getRavine("urn:ngsi-ld:Ravine:001")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:Ravine:001'},
 'name': {'type': 'literal', 'value': 'Ravine 06A01'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressLocality': {'type': 'literal',
  'value': 'RM-F35, La Puebla, Cartagena'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'postal': {'type': 'literal', 'value': '30395'},
 'source': {'type': 'literal',
  'value': 'https://saihweb.chsegura.es/apps/iVisor/visor_variable.php?punto=06A01U12'},
 'description': {'type': 'literal',
  'value': 'Control frame 06A01 in La Puebla, Rambla del Albujon.'},
 'coordinates1': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '37.7207e0'},
 'coordinates2': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '-0.9144e0'}}

In [112]:
getWaterNetwork("urn:ngsi-ld:WaterNetwork:000")

{'name': {'type': 'literal', 'value': 'Rambla del Albuj\\u00f3n'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'description': {'type': 'literal',
  'value': 'Una de las ramblas mas importantes de la Regi\\u00f3n compuesta a su vez por un conjunto de otras ramblas'},
 'location': {'type': 'bnode', 'value': 'b0'},
 'isComposedOf': {'type': 'literal',
  'value': 'urn:ngsi-ld:Ravine:002,urn:ngsi-ld:Ravine:005,urn:ngsi-ld:Ravine:004,urn:ngsi-ld:Ravine:003,urn:ngsi-ld:Ravine:006,urn:ngsi-ld:Ravine:007,urn:ngsi-ld:Ravine:001'}}

In [92]:
getSoundingPlace("urn:ngsi-ld:SoundingPlace:001")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:SoundingPlace:001'},
 'name': {'type': 'literal', 'value': 'Sounding Place 06Z02'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressLocality': {'type': 'literal', 'value': 'F-34, Cartagena'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'postal': {'type': 'literal', 'value': '30383'},
 'source': {'type': 'literal',
  'value': 'https://saihweb.chsegura.es/apps/iVisor/visor_variable.php?punto=06Z02E10'},
 'description': {'type': 'literal',
  'value': 'Sounding Place 06Z02 which belong to the Piezometric Network in Mar Menor'},
 'coordinates1': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '37.64266e0'},
 'coordinates2': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '-0.777275e0'}}

In [93]:
getDeviceMeasurement("urn:ngsi-ld:DeviceMeasurement:060")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:DeviceMeasurement:060'},
 'name': {'type': 'literal', 'value': 'DeviceMeasurement 060'},
 'source': {'type': 'literal',
  'value': 'https://idearm.imida.es/cgi/siomctdmarmenor/#CTD-E1'},
 'controlledProperty': {'type': 'literal', 'value': 'turbidity'},
 'deviceType': {'type': 'literal', 'value': 'TurbiditySensor'},
 'numValue': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
  'value': '-99'},
 'observedAt': {'type': 'literal',
  'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
  'value': '2016-08-02T00:00:00.000Z'},
 'depth': {'type': 'literal',
  'datatype': 'http://www.w3.org/2001/XMLSchema#double',
  'value': '-0.8e0'},
 'refDevice': {'type': 'uri', 'value': 'urn:ngsi-ld:Device:000'}}

In [94]:
getDevice("urn:ngsi-ld:Device:001")

{'entity': {'type': 'uri', 'value': 'urn:ngsi-ld:Device:001'},
 'name': {'type': 'literal', 'value': 'Buoy E10 found in Mar Menor'},
 'addressCountry': {'type': 'literal', 'value': 'ES'},
 'addressLocality': {'type': 'literal',
  'value': 'Mar Menor, Los Nietos, Cartagena'},
 'addressRegion': {'type': 'literal', 'value': 'Murcia'},
 'postalCode': {'type': 'literal', 'value': '30383'},
 'controlledProperties': {'type': 'literal',
  'value': 'chlorophyll,conductivity,organicMatter,oxygen,pH,polyethylene,salinity,temperature,transparency,turbidity'},
 'controlledAsset': {'type': 'uri', 'value': 'urn:ngsi-ld:Buoy:001'},
 'deviceCategory': {'type': 'literal', 'value': 'sensor'},
 'alternateName': {'type': 'literal', 'value': 'Device001 for Buoy 001'},
 'areaServed': {'type': 'literal', 'value': 'Mar Menor'},
 'dateLastValueReported': {'type': 'literal', 'value': '2023-08-24T00:00:00Z'},
 'source': {'type': 'literal',
  'value': 'https://idearm.imida.es/cgi/siomctdmarmenor/#CTD-E10'},
 'desc

In [95]:
getDeviceControlledProperties("urn:ngsi-ld:Device:001")

['chlorophyll',
 'conductivity',
 'organicMatter',
 'oxygen',
 'pH',
 'polyethylene',
 'salinity',
 'temperature',
 'transparency',
 'turbidity']

In [96]:
getEntityControlledProperties("urn:ngsi-ld:Buoy:001")

['chlorophyll',
 'conductivity',
 'organicMatter',
 'oxygen',
 'pH',
 'polyethylene',
 'salinity',
 'temperature',
 'transparency',
 'turbidity']

### Creamos las subscripciones a Orion

Ahora se va a crear una serie de subscripciones en Orion para que notifique ante cualquier cambio en la entidad de Orion a nuestro servido NODE que tenemos desplegado, y este realice una actualización en nuestro SparQL.

In [49]:
crear_subscription("Subscription Buoy", "Buoy", "http://node-app:3000/historic/subscription/Buoy","http://localhost:1026/ngsi-ld/v1/subscriptions/")
crear_subscription("Subscription SoundingPlace", "SoundingPlace", "http://node-app:3000/historic/subscription/SoundingPlace","http://localhost:1026/ngsi-ld/v1/subscriptions/")
crear_subscription("Subscription Ravine", "Ravine", "http://node-app:3000/historic/subscription/Ravine","http://localhost:1026/ngsi-ld/v1/subscriptions/")
crear_subscription("Subscription DeviceMeasurement", "DeviceMeasurement", "http://node-app:3000/historic/subscription/DeviceMeasurement/filtered",
                   "http://localhost:1026/ngsi-ld/v1/subscriptions/", sent_attributes=["numValue","dateLastValueReported"], watched_attributes=["numValue"])
crear_subscription("Subscription DeviceMeasurement", "DeviceMeasurement", "http://node-app:3000/historic/subscription/DeviceMeasurement",
                   "http://localhost:1026/ngsi-ld/v1/subscriptions/", 
                   sent_attributes=["identifier","deviceType","controlledProperty","refDevice","source","name","depth","target"], 
                   watched_attributes=["identifier","deviceType","controlledProperty","refDevice","source","name","depth","target"])

<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>


### Creación de una nueva relación

En este caso, una posible propiedad interesante a añadir sería `measurements` (ids de los DeviceMeasurements) dentro de las propias entidades principales (Buoy, SoundingPlace, Ravine), de esta forma a la hora de obtener los valores de las mediciones de una entidad no tendríamos que realizar dos pasos (primero obtener su Device asociado, y luego los DeviceMeasurements asociados a ese Device). 

![Modelado Mar Menor](./esquema_orion_fuseki.png)

#### Creacion relacion con todos sus DeviceMeasurement

In [42]:
add_measurements_to_entity("urn:ngsi-ld:Buoy:003")

{'statusCode': 200, 'message': 'Update succeeded'}

In [46]:
get_values_measurements("urn:ngsi-ld:Buoy:003")

[{'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '191.92e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '0'}},
 {'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '135.51e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '-1'}},
 {'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '123.46e0'},
  'controlledProperty': 

#### Creacion relacion con todos sus DeviceMeasurement que controlen una propiedad concreta

In [47]:
add_measurements_controlled_property_to_entity("urn:ngsi-ld:Buoy:000","temperature")

{'statusCode': 200, 'message': 'Update succeeded'}

In [48]:
get_values_measurements_controlled("urn:ngsi-ld:Buoy:000","temperature")

[{'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '30.86e0'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '0'}},
 {'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '-99'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '-1'}},
 {'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '30.8e0'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'dat

### Prueba para ver que se modifican las entidades en Fuseki

Para comprobar que la actualización de los datos a traves de las subscripciones creadas funcione vamos a probar a realizar una modificación sobre una de las mediciones de la Boya 003 en nuestro Orion Context Broker para ver si efectivamente se refleja el cambio en Fuseki.

In [57]:
get_values_measurements("urn:ngsi-ld:Buoy:003")

[{'measurement': {'type': 'uri', 'value': 'urn:ngsi-ld:DeviceMeasurement:240'},
  'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '191.92e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '0'}},
 {'measurement': {'type': 'uri', 'value': 'urn:ngsi-ld:DeviceMeasurement:241'},
  'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '135.51e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
 

Realizamos la modificacion

In [58]:
modify_device_measurement(
    value=12,
    observedAt="2023-08-25T00:00:00.000Z",
    unitcode=None,
    url="http://localhost:1026/ngsi-ld/v1/entities/urn:ngsi-ld:DeviceMeasurement:240/attrs",
    depth=0
)

modify_content
{'numValue': {'type': 'Property', 'value': 12, 'observedAt': '2023-08-25T00:00:00.000Z', 'depth': {'type': 'Property', 'value': 0}}, 'dateLastValueReported': {'type': 'Property', 'value': '2023-08-25T00:00:00.000Z'}}
204


Podemos comprobar que el valor se h modificado justo como debería de ocurrir

In [59]:
get_values_measurements("urn:ngsi-ld:Buoy:003")

[{'measurement': {'type': 'uri', 'value': 'urn:ngsi-ld:DeviceMeasurement:240'},
  'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '12.0e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-25T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   'value': '0'}},
 {'measurement': {'type': 'uri', 'value': 'urn:ngsi-ld:DeviceMeasurement:241'},
  'numValue': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#double',
   'value': '135.51e0'},
  'controlledProperty': {'type': 'literal', 'value': 'polyethylene'},
  'observedAt': {'type': 'literal',
   'datatype': 'https://uri.etsi.org/ngsi-ld/DateTime',
   'value': '2023-08-24T00:00:00.000Z'},
  'depth': {'type': 'literal',
   'datatype': 'http://www.w3.org/2001/XMLSchema#integer',
   

### Prueba de alguna consulta simple

Se han creado dos consultas para mostrar ejemplos de enfoques posibles, en primer lugar se ha hecho una busqueda de un parametro concreto, de tal forma que no es necesario aportar información como el prefijo o nombre de la propiedad a consultar y luego un enfoque mas generico en el que se especifican estos parametros pero nos permite realizar consultas genericas.

Luego hay un metodo para filtrar por parametros que sean propiedades o relaciones

In [100]:
query_by_name("Buoy E10")

['urn:ngsi-ld:Device:001', 'urn:ngsi-ld:Buoy:001']

In [101]:
query_sparql_by_poperty_parameter("https://smartdatamodels.org/dataModel.DeviceMeasurement/","numValue","45.57")

['urn:ngsi-ld:DeviceMeasurement:002', 'urn:ngsi-ld:DeviceMeasurement:001']

In [108]:
query_sparql_by_relation_parameter("https://smartdatamodels.org/dataModel.DeviceMeasurement/", "refDevice", "urn:ngsi-ld:Device:010")

['urn:ngsi-ld:DeviceMeasurement:1122',
 'urn:ngsi-ld:DeviceMeasurement:1166',
 'urn:ngsi-ld:DeviceMeasurement:1134',
 'urn:ngsi-ld:DeviceMeasurement:1102',
 'urn:ngsi-ld:DeviceMeasurement:1146',
 'urn:ngsi-ld:DeviceMeasurement:1114',
 'urn:ngsi-ld:DeviceMeasurement:1158',
 'urn:ngsi-ld:DeviceMeasurement:1126',
 'urn:ngsi-ld:DeviceMeasurement:1138',
 'urn:ngsi-ld:DeviceMeasurement:1106',
 'urn:ngsi-ld:DeviceMeasurement:1118',
 'urn:ngsi-ld:DeviceMeasurement:1092',
 'urn:ngsi-ld:DeviceMeasurement:1161',
 'urn:ngsi-ld:DeviceMeasurement:1096',
 'urn:ngsi-ld:DeviceMeasurement:1141',
 'urn:ngsi-ld:DeviceMeasurement:1153',
 'urn:ngsi-ld:DeviceMeasurement:1121',
 'urn:ngsi-ld:DeviceMeasurement:1165',
 'urn:ngsi-ld:DeviceMeasurement:1133',
 'urn:ngsi-ld:DeviceMeasurement:1101',
 'urn:ngsi-ld:DeviceMeasurement:1145',
 'urn:ngsi-ld:DeviceMeasurement:1113',
 'urn:ngsi-ld:DeviceMeasurement:1157',
 'urn:ngsi-ld:DeviceMeasurement:1125',
 'urn:ngsi-ld:DeviceMeasurement:1169',
 'urn:ngsi-ld:DeviceMeasu